In [1]:
from datasketch import MinHash, MinHashLSH
import json
import numpy as np

In [33]:
#we have kept the venue and list of authors as a dictionary and savced it in a text file
js = {}
with open('venue_name.txt') as f:     #read the file and save it into a dictionary
    data = f.read()
    
js = json.loads(data)

In [3]:
l4 = list(js.keys())
len(l4)

138575

In [34]:
l1 = list(js.keys())
len(l1)

138575

In [35]:
def shingles(l1, k):
    dataset = []
    universal_list =[]
    
    count=0
    for document in l1:
#         reference = (" ".join(document))    #join all references and make into a single one so that we can genrate shingles
        ele = document
        temp =[]

        single_ref_list = list(ele.split(" "))  #add every word into a list
        for ptr in range(0, len(single_ref_list)-k+1):   #perform slicing window word wise with window size as k till end of list
            temp_val = single_ref_list[ptr:(ptr+k):1]   
            temp_val = (" ".join(temp_val))  #merge the words in the window into a string ==> this will be a shingle
            temp.append(temp_val)  #append the shingle to the lost of shi ngles for that document
                
        dataset.append(temp)  #append the list to the main dataset of shingles
        print("dataset iteration number ======> " + str(count))
        count = count+1
            
            
    print()   
    print('----------------------------')   
                 
    
    return dataset


In [54]:
dataset1 = shingles(l1, 2)       #for this part of assignment we have set the shingling paramter to 2

dataset iteration number ======> 0
dataset iteration number ======> 1
dataset iteration number ======> 2
dataset iteration number ======> 3
dataset iteration number ======> 4
dataset iteration number ======> 5
dataset iteration number ======> 6
dataset iteration number ======> 7
dataset iteration number ======> 8
dataset iteration number ======> 9
dataset iteration number ======> 10
dataset iteration number ======> 11
dataset iteration number ======> 12
dataset iteration number ======> 13
dataset iteration number ======> 14
dataset iteration number ======> 15
dataset iteration number ======> 16
dataset iteration number ======> 17
dataset iteration number ======> 18
dataset iteration number ======> 19
dataset iteration number ======> 20
dataset iteration number ======> 21
dataset iteration number ======> 22
dataset iteration number ======> 23
dataset iteration number ======> 24
dataset iteration number ======> 25
dataset iteration number ======> 26
dataset iteration number ======> 27
da

In [55]:
dataset1

[[],
 ['J. Amer.', 'Amer. Math.', 'Math. Soc'],
 ['Notices Amer.', 'Amer. Math.', 'Math. Soc'],
 ['Journal of',
  'of Combinatorial',
  'Combinatorial Theory',
  'Theory Series',
  'Series A'],
 ['Operations Research'],
 [],
 [],
 [],
 ['The PageRank',
  'PageRank citation',
  'citation ranking:',
  'ranking: Bringing',
  'Bringing order',
  'order to',
  'to the',
  'the web'],
 ['IEEE J.', 'J. Select.', 'Select. Areas', 'Areas Commun'],
 ['IEEE Wireless', 'Wireless Commun'],
 ['IEEE Trans.', 'Trans. Inform.', 'Inform. Theory'],
 ['Informationtheoretical results',
  'results for',
  'for the',
  'the discrete',
  'discrete memoryless',
  'memoryless multiple',
  'multiple access',
  'access channel'],
 [],
 [],
 [],
 ['Neural Networks'],
 ['IEEE Trans.', 'Trans. on', 'on Circuits', 'Circuits and', 'and Systems'],
 [],
 [],
 [],
 [],
 ['Philosophical Transactions',
  'Transactions of',
  'of the',
  'the Royal',
  'Royal Society',
  'Society of',
  'of London,',
  'London, Series',
  '

In [56]:

dataset = []
for i in dataset1:
    dataset.append(set(i))

len(dataset)

35229

In [57]:
hashFunctions = []   #stors hash functions here
for i in range(0, len(l1)):
    hashFunctions.append(MinHash(num_perm=128))     #generate and append hashfunctions for all the documents

len(hashFunctions)

35229

In [58]:
for i in range(0, len(l1)):
    hashFunctions[i]= MinHash(num_perm=128)
    for token in dataset[i]:
        hashFunctions[i].update(token.encode('utf8'))     #update the hashfunction as per the shingles

In [59]:
count_list ={}
matched_dict =[]
thresh_list = [0.60]
# c= 0.25
# while c <=0.62:
#     val = round(c, 2)
#     thresh_list.append(val)     #generate the list of references starting from 25% and increase threshold by 2% in every iteration
#     c= c+ 0.02

for thr in thresh_list:
    thres = thr
    lsh = MinHashLSH(threshold=thres, num_perm=128)     #vary threshold on the values defined above

    for i in range(0, len(hashFunctions)):
            temp = i
            lsh.insert(temp, hashFunctions[i])     #insert the hashes into lsh

    dict ={}
    for i in range(0, len(hashFunctions)):
        result = lsh.query(hashFunctions[i])    #run the query for all the documents to obtain the candidate pairs
        if len(result)>1:
            result.remove(i)
            dict[i] = result

    key = dict.keys()

    for j, k in dict.items():
    
        val_list = dict[j]
        val_list2 = set(val_list)
        for i in k:
            if i in key:
                val = set(dict[i])
                val = val - val_list2    #here we are eleminating the duplicate pairs
                val.remove(j)
                dict[i]=val
            
    remove_list = []         

    for i, j in dict.items():
        if j == set():
            remove_list.append(i)     #find the sets which are empty from the list of candidate pairs
        
    for i in remove_list:
        dict.pop(i)    #remove empty sets from the list of candidate pairs
        
    val1 ={}
    val1[thr] = dict
    matched_dict.append(val1)     #storing the papers which matched
    
    candidate_pair = len(dict.keys())
    count_list[thres] = candidate_pair    #storing the count of candidate pairs
    
    print(thr)


0.6


In [60]:
print(count_list)

{0.6: 16383}


In [61]:
matched_dict

[{0.6: {0: [8193,
    8194,
    8195,
    8196,
    5,
    6,
    7,
    8198,
    8200,
    24581,
    24582,
    24588,
    13,
    14,
    15,
    24591,
    24592,
    18,
    19,
    20,
    21,
    24593,
    32790,
    24604,
    8223,
    32,
    8226,
    8227,
    8228,
    37,
    8229,
    39,
    8230,
    16418,
    24613,
    32812,
    8237,
    32813,
    24623,
    8240,
    32816,
    32821,
    8246,
    32824,
    8249,
    59,
    8251,
    24636,
    8269,
    78,
    24655,
    32847,
    8273,
    24658,
    24659,
    8276,
    85,
    8277,
    8278,
    24660,
    8281,
    24661,
    8283,
    8284,
    8285,
    24668,
    8287,
    8288,
    24672,
    103,
    109,
    24690,
    24691,
    116,
    16502,
    32886,
    32888,
    32889,
    32890,
    32891,
    32892,
    32893,
    16510,
    32894,
    24707,
    24714,
    24715,
    24716,
    8336,
    8337,
    148,
    155,
    156,
    16541,
    167,
    24746,
    171,
    8365,
    24752,
 

In [62]:
i = matched_dict[0]
v = i.values()
temp=[]
k=[]
count=0
for i in v:
    temp = list(i.values())
    k = list(i.keys())

for i in temp:
    count = count + len(i)
    
count
# v

48406

In [63]:
ind  = k.index(1270)
l1[k[ind]]

"FOCS '02: Proceedings of the 43rd Symposium on Foundations of Computer Science"

In [64]:
for i in temp[ind]:
    print(l1[i])
    
len(temp[ind])

Proceedings of the 43rd Symposium on Foundations of Computer Science (FOCS'02)
Proceedings of the 43rd Symposium on Foundations of Computer Science, ser. FOCS '02


2

In [65]:
s1 = set(k)
s2 =[]
for i in temp:
    s2 = s2 + list(i)
s3 = set(s2)
len(s3)

26366

In [66]:
s3 = s3.union(s1)
len(s3)

35229

In [67]:
l2 = list(np.arange(0, 138575,1))
l2

[0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,


In [68]:
s3 = list(s3)
for i in s3:
    l2.remove(i)
len(l2)
l2.sort(reverse=True)

In [69]:
for i in l2:
#     if i<len(l1):
    l1.pop(i)
len(l1)

IndexError: pop index out of range

In [70]:
len(l1)

35229

In [53]:
l1

['Combinatorica',
 'J. Amer. Math. Soc',
 'Notices Amer. Math. Soc',
 'Journal of Combinatorial Theory Series A',
 'Operations Research',
 'Science',
 'SIGIR',
 'CSCW',
 'The PageRank citation ranking: Bringing order to the web',
 'IEEE J. Select. Areas Commun',
 'IEEE Wireless Commun',
 'IEEE Trans. Inform. Theory',
 'Informationtheoretical results for the discrete memoryless multiple access channel',
 "ECAL'03",
 '',
 "SAB'06",
 'Neural Networks',
 'IEEE Trans. on Circuits and Systems',
 'GECCO',
 "EuroGP'00",
 'LNCS',
 "SIGGRAPH'94",
 'Philosophical Transactions of the Royal Society of London, Series B, Biological sciences',
 'Mechanical Systems and Signal Processing',
 'Journal of Mechanical Design',
 'Journal of Chemical Physics',
 'IEEE Trans. Wireless Commun',
 'IEEE Trans. Inf. Theory',
 'IEEE J. Sel. Areas Commun',
 'Foundations and Trends in Commun. and Inf. Theory',
 'Proc. IEEE Int. Symp. Inf. Theory (ISIT)',
 'Handbook of Mathematical Functions',
 'INRIA',
 'Artificial Int

In [145]:
with open(r'C:/Users/hp/Big Data Analytics (BDA)/unique_venue.txt', 'w') as fp:
    fp.write('\n'.join(l1))

In [71]:
matches = {}
for i in range(0, len(k)):
    matches[k[i]] = temp[i]
matches

{0: [8193,
  8194,
  8195,
  8196,
  5,
  6,
  7,
  8198,
  8200,
  24581,
  24582,
  24588,
  13,
  14,
  15,
  24591,
  24592,
  18,
  19,
  20,
  21,
  24593,
  32790,
  24604,
  8223,
  32,
  8226,
  8227,
  8228,
  37,
  8229,
  39,
  8230,
  16418,
  24613,
  32812,
  8237,
  32813,
  24623,
  8240,
  32816,
  32821,
  8246,
  32824,
  8249,
  59,
  8251,
  24636,
  8269,
  78,
  24655,
  32847,
  8273,
  24658,
  24659,
  8276,
  85,
  8277,
  8278,
  24660,
  8281,
  24661,
  8283,
  8284,
  8285,
  24668,
  8287,
  8288,
  24672,
  103,
  109,
  24690,
  24691,
  116,
  16502,
  32886,
  32888,
  32889,
  32890,
  32891,
  32892,
  32893,
  16510,
  32894,
  24707,
  24714,
  24715,
  24716,
  8336,
  8337,
  148,
  155,
  156,
  16541,
  167,
  24746,
  171,
  8365,
  24752,
  180,
  183,
  186,
  190,
  32970,
  32973,
  24782,
  32975,
  32977,
  32978,
  24787,
  32979,
  24789,
  24790,
  32980,
  32981,
  24797,
  24798,
  16607,
  32991,
  32994,
  24804,
  24806,
  238

In [152]:
# with open('matched_venue.txt', 'w') as fp:
#      fp.write(json.dumps(matches))
with open('matched_venue.txt','w') as fp: 
      fp.write(str(matches))

In [72]:
for k,v in matches.items():
    for i in v:
        l1[i] = l1[k]

In [73]:
l1

['Combinatorica',
 'J. Amer. Math. Soc',
 'Notices Amer. Math. Soc',
 'Journal of Combinatorial Theory Series A',
 'Operations Research',
 'Combinatorica',
 'Combinatorica',
 'Combinatorica',
 'The PageRank citation ranking: Bringing order to the web',
 'IEEE J. Select. Areas Commun',
 'IEEE Wireless Commun',
 'IEEE Trans. Inform. Theory',
 'Informationtheoretical results for the discrete memoryless multiple access channel',
 'Combinatorica',
 'Combinatorica',
 'Combinatorica',
 'Neural Networks',
 'IEEE Trans. on Circuits and Systems',
 'Combinatorica',
 'Combinatorica',
 'Combinatorica',
 'Combinatorica',
 'Philosophical Transactions of the Royal Society of London, Series B, Biological sciences',
 'Mechanical Systems and Signal Processing',
 'Journal of Mechanical Design',
 'Journal of Chemical Physics',
 'IEEE Trans. Wireless Commun',
 'IEEE Trans. Inf. Theory',
 'IEEE J. Sel. Areas Commun',
 'Foundations and Trends in Commun. and Inf. Theory',
 'Proc. IEEE Int. Symp. Inf. Theory (I

In [156]:
with open(r'C:/Users/hp/Big Data Analytics (BDA)/Assignment3_question2_dataset.txt', 'w') as fp:
    fp.write('\n'.join(l1))

In [74]:
len(l1)

35229

In [75]:
len(set(l1))

8863

In [25]:
new_l1 = []
with open(r'C:/Users/hp/Big Data Analytics (BDA)/unique_venue.txt', 'r') as fp:
    for line in fp:
        x = line[:-1]
        new_l1.append(x)

print(new_l1)

['Combinatorica', 'J. Amer. Math. Soc', 'Notices Amer. Math. Soc', 'Journal of Combinatorial Theory Series A', 'Operations Research', 'Science', 'SIGIR', 'CSCW', 'The PageRank citation ranking: Bringing order to the web', 'IEEE J. Select. Areas Commun', 'IEEE Wireless Commun', 'IEEE Trans. Inform. Theory', 'Informationtheoretical results for the discrete memoryless multiple access channel', "ECAL'03", '', "SAB'06", 'Neural Networks', 'IEEE Trans. on Circuits and Systems', 'GECCO', "EuroGP'00", 'LNCS', "SIGGRAPH'94", 'Philosophical Transactions of the Royal Society of London, Series B, Biological sciences', 'Mechanical Systems and Signal Processing', 'Journal of Mechanical Design', 'Journal of Chemical Physics', 'IEEE Trans. Wireless Commun', 'IEEE Trans. Inf. Theory', 'IEEE J. Sel. Areas Commun', 'Foundations and Trends in Commun. and Inf. Theory', 'Proc. IEEE Int. Symp. Inf. Theory (ISIT)', 'Handbook of Mathematical Functions', 'INRIA', 'Artificial Intelligence in Medicine', 'Medical 

In [26]:
new_dict={}
for k, v in js.items():
    if k in new_l1:
        new_dict[k] = v
new_dict

{'Combinatorica': ['N Karmarkar',
  'N Karmarkar',
  'J F Geelen',
  'S Iwata',
  'E SzemerÃ©di',
  'W T Trotter',
  'E D',
  'M Hajiaghayi',
  'M Grohe',
  'N Karmarkar',
  'Noam Nisan',
  'V Grolmusz',
  'N Alon',
  'E Fischer',
  'M Krivelevich',
  'M Szegedy',
  'L Babai',
  'D Conlon',
  'J Fox',
  'B Sudakov',
  'P ErdÅ‘s',
  'Nathan Linial',
  'Eran London',
  'Yuri Rabinovich',
  'N Alon',
  'E Fischer',
  'M Krivelevich',
  'M Szegedy',
  'A Frieze',
  'R Kannan',
  'J KomlÃ³s',
  'G N SÃ¡rkÃ¶zy',
  'E SzemerÃ©di',
  'C H Papadimitriou',
  'S Vempala',
  'JÃ³zsef Beck',
  'Endre SzemerÃ©di',
  'William T Trotter',
  'B L Rothschild',
  'E G Straus',
  'B Mckay',
  'N Wormald',
  'A Frank',
  'J C Lagarias',
  'H W Lenstra',
  ' Jr',
  'C P Schnorr',
  'Noam Nisan',
  'Avi Wigderson',
  'Robert Brignall',
  'Sophie Huczynska',
  'Vincent Vatter',
  'P Raghavan',
  'C D Thompson',
  'H De Fraysseix',
  'J Pach',
  'R Pollack',
  'B Herwig',
  'L Babai',
  ' Fernandez De La',
  '

In [27]:
len(new_dict.keys())

35228

In [76]:
merged_dict={}
for k, v in matches.items():
    key = new_l1[k]
    val=[]
    for i in list(v):
        key_new = new_l1[i]
        if key_new in js.keys():
            val = val + js[key_new]
    merged_dict[key] = val

merged_dict

{'Combinatorica': ['B Carterette',
  'E Kanoulas',
  'M M Hall',
  'P D Clough',
  'Enrique Alfonseca',
  'Marco De Boni',
  'JosÃ©-Luis Jara- Valencia',
  'Suresh Manandhar',
  'Ellen M Voorhees',
  'Ellen M Voorhees',
  'K Roberts',
  'M S Simpson',
  'E M Voorhees',
  'W R Hersh',
  'E M Voorhees',
  'D M Tice',
  'E M Voorhees',
  'D M Tice',
  ' Harabagiu',
  'J Luo',
  'X Dong',
  'H Yang',
  'S Clinchant',
  'Ã‰ Gaussier',
  'D Metzler',
  'W B Croft',
  'H Yang',
  'D Guan',
  'S Zhang',
  'Chengxiang Zhai',
  'John La Erty',
  'Norbert Fuhr',
  ' Finkelstein',
  'Kalervo JÃ¤rvelin',
  'Jaana KekÃ¤lÃ¤inen',
  'E Garfield',
  'S Kirkpatrick',
  'C D Gelatt',
  'M P Vecchi',
  'A BarabÃ¡si',
  'R Albert',
  'M Balter',
  'L M Adleman',
  'G L Gerstein',
  'D H Perkel',
  'W Bialek',
  'F Rieke',
  'R R De Ruyter Van Steveninck',
  'D Warland',
  'Y Ikegaya',
  'G Aaron',
  'R Cossart',
  'D Aronov',
  'I Lampl',
  'D Ferster',
  'R Yuste',
  'A L BarabÃ¡si',
  'R Albert',
  'J B 

In [77]:
len(merged_dict.keys())

16383

In [80]:
import pickle         

f = open("assignment3_Q1_pickle", "x")               #create a file named result to store our data structure

with open('assignment3_Q1_pickle', 'wb') as f:
  pickle.dump(merged_dict, f)      # dump method is used to save variables (data structure we created in our case) to a pickle file.

In [81]:
with open('assignment3_Q1_pickle', 'rb') as f:
   res = pickle.load(f)               # load method is used to load the contents of a pickle file

   print(res)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [85]:
values = list(res.values())
values[0]

['B Carterette',
 'E Kanoulas',
 'M M Hall',
 'P D Clough',
 'Enrique Alfonseca',
 'Marco De Boni',
 'JosÃ©-Luis Jara- Valencia',
 'Suresh Manandhar',
 'Ellen M Voorhees',
 'Ellen M Voorhees',
 'K Roberts',
 'M S Simpson',
 'E M Voorhees',
 'W R Hersh',
 'E M Voorhees',
 'D M Tice',
 'E M Voorhees',
 'D M Tice',
 ' Harabagiu',
 'J Luo',
 'X Dong',
 'H Yang',
 'S Clinchant',
 'Ã‰ Gaussier',
 'D Metzler',
 'W B Croft',
 'H Yang',
 'D Guan',
 'S Zhang',
 'Chengxiang Zhai',
 'John La Erty',
 'Norbert Fuhr',
 ' Finkelstein',
 'Kalervo JÃ¤rvelin',
 'Jaana KekÃ¤lÃ¤inen',
 'E Garfield',
 'S Kirkpatrick',
 'C D Gelatt',
 'M P Vecchi',
 'A BarabÃ¡si',
 'R Albert',
 'M Balter',
 'L M Adleman',
 'G L Gerstein',
 'D H Perkel',
 'W Bialek',
 'F Rieke',
 'R R De Ruyter Van Steveninck',
 'D Warland',
 'Y Ikegaya',
 'G Aaron',
 'R Cossart',
 'D Aronov',
 'I Lampl',
 'D Ferster',
 'R Yuste',
 'A L BarabÃ¡si',
 'R Albert',
 'J B Tenenbaum',
 'V Silva',
 'J C Langford',
 'M MÃ©zard',
 'G Parisi',
 'R Zecc

In [167]:
with open('Assignment3_question1_dataset.txt','w') as fp: 
      fp.write(str(merged_dict))

In [3]:
!pip install dgim

In [16]:
from dgim import Dgim
dgim = Dgim(N=500, error_rate=0.1)
for i in range(500):
    if i%2==0:
        dgim.update(False)
    else:
        dgim.update(True)
dgim_result = dgim.get_count() # 30 (exact result is 32)

In [15]:
dgim_result

15